In [1]:
import pandas as pd
import seaborn as sns
import numpy as np

In [188]:
users = pd.read_csv('data/users_cleaned.csv')
users.head()

username  user_id  user_watching  user_completed  user_onhold  \
0        karthiga  2255153              3              49            1   
1       Damonashu    37326             45             195           27   
2           bskai   228342             25             414            2   
3  terune_uzumaki   327311              5               5            0   
4           Bas_G  5015094             35             114            6   

   user_dropped  user_plantowatch  user_days_spent_watching  gender  \
0             0                 0                 55.091667  Female   
1            25                59                 82.574306    Male   
2             5                11                159.483333    Male   
3             0                 0                 11.394444  Female   
4            20               175                 30.458333    Male   

              location           birth_date  access_rank            join_date  \
0      Chennai, India   1990-04-29 00:00:00          NaN  2013-03-03 00:00:00   
1     Detroit,Michigan  1991-08-01 00:00:00          NaN  2008-02-13 00:00:00   
2      Nayarit, Mexico  1990-12-14 00:00:00          NaN  2009-08-31 00:00:00   
3    Malaysia, Kuantan  1998-08-24 00:00:00          NaN  2010-05-10 00:00:00   
4  Nijmegen, Nederland  1999-10-24 00:00:00          NaN  2015-11-26 00:00:00   

           last_online  stats_mean_score  stats_rewatched  stats_episodes  
0  2014-02-04 01:32:00              7.43              0.0            3391  
1  2017-07-10 06:52:54              6.15              6.0            4903  
2  2014-05-12 16:35:00              8.27              1.0            9701  
3  2012-10-18 19:06:00              9.70              6.0             697  
4  2018-05-10 20:53:37              7.86              0.0            1847

### Extract using Regex

In [189]:
users['t1'] = users['location'].str.split(',').str[0]
users['t2'] = users['location'].str.split(',').str[1]
users[['location','t1','t2']].head(20)

location                    t1          t2
0        Chennai, India                Chennai      India 
1       Detroit,Michigan               Detroit    Michigan
2        Nayarit, Mexico               Nayarit      Mexico
3      Malaysia, Kuantan              Malaysia     Kuantan
4    Nijmegen, Nederland              Nijmegen   Nederland
5                 Poland                Poland         NaN
6         Norberg Sweden        Norberg Sweden         NaN
7                 Poland                Poland         NaN
8               Nebraska              Nebraska         NaN
9     England,Manchester               England  Manchester
10           ~ Hungary ~           ~ Hungary ~         NaN
11        United Kingdom        United Kingdom         NaN
12                  home                  home         NaN
13            California            California         NaN
14                Mexico                Mexico         NaN
15      Hamilton Ontario      Hamilton Ontario         NaN
16           Chicago, IL               Chicago          IL
17          San Jose, CA              San Jose          CA
18  somewhere really hot  somewhere really hot         NaN
19                 Guess                 Guess         NaN

In [190]:
len(users)

108711

### Pass in value to Geopy and extract location

In [191]:
# Install a pip package in the current Jupyter kernel
import sys
!{sys.executable} -m pip install geopy

distributed 1.21.8 requires msgpack, which is not installed.
You are using pip version 10.0.1, however version 20.3b1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [192]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="fulldata_alchemist")

# Test
location = geolocator.geocode("Detroit, Michigan")
print(location.address)
print(location.raw)
# print(location.country)

Detroit, Wayne County, Michigan, United States of America
{'place_id': 234855498, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 134591, 'boundingbox': ['42.255192', '42.4502432', '-83.287959', '-82.9104391'], 'lat': '42.3315509', 'lon': '-83.0466403', 'display_name': 'Detroit, Wayne County, Michigan, United States of America', 'class': 'boundary', 'type': 'administrative', 'importance': 0.8968259938952166, 'icon': 'https://nominatim.openstreetmap.org/ui/mapicons//poi_boundary_administrative.p.20.png'}


In [193]:
# Splitting string by comma, getting first index as city, last index as country, stripping of white spaces on edges
city = location.address.split(',')[0].strip()
country = location.address.split(',')[-1].strip()

In [194]:
city

'Detroit'

In [195]:
country

'United States of America'

In [196]:
from geopy.extra.rate_limiter import RateLimiter
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=2)

In [139]:
users['city'] = users['location'].apply(geolocator.geocode).address.split(',')[0].strip()
users['country'] = users['location'].apply(geolocator.geocode).address.split(',')[-1].strip()

GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /search?q=C-Town%2C+Sachsen&format=json&limit=1 (Caused by ReadTimeoutError("HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Read timed out. (read timeout=1)",))

In [ ]:
from geopy.exc import GeocoderTimedOut
import geopy

def do_geocode(address, attempt=1, max_attempts=5):
    try:
        return geolocator.geocode(address)
    except GeocoderTimedOut:
        if attempt <= max_attempts:
            return do_geocode(address, attempt=attempt+1)
        raise

users['city'] = users['location'].apply(do_geocode).address.split(',')[0].strip()

- 106K rows of requests, with 1sec/request rate limiter, it'll take 73 hours to get full results. Not worth

### Using csv of major cities and countries

In [197]:
world_cities = pd.read_csv('worldcities.csv')

In [198]:
world_cities.head()

city city_ascii      lat       lng      country iso2 iso3   admin_name  \
0    Tokyo      Tokyo  35.6897  139.6922        Japan   JP  JPN        Tōkyō   
1  Jakarta    Jakarta  -6.2146  106.8451    Indonesia   ID  IDN      Jakarta   
2    Delhi      Delhi  28.6600   77.2300        India   IN  IND        Delhi   
3   Mumbai     Mumbai  18.9667   72.8333        India   IN  IND  Mahārāshtra   
4   Manila     Manila  14.5958  120.9772  Philippines   PH  PHL       Manila   

   capital  population          id  
0  primary  37977000.0  1392685764  
1  primary  34540000.0  1360771077  
2    admin  29617000.0  1356872604  
3    admin  23355000.0  1356226629  
4  primary  23088000.0  1608618140

In [199]:
users['location']
found = (users[users['location'].str.contains('chennai', na=False)])
found.head(5)

username  user_id  user_watching  user_completed  user_onhold  \
26837   sasidharan408  3656519             57            1206          127   
28419  emiya_kisuke97  5745873             11             119            6   
87828      muthubasha  4498210             28             169            4   

       user_dropped  user_plantowatch  user_days_spent_watching gender  \
26837           507               614                333.593773   Male   
28419             3                55                 77.922222   Male   
87828            10                30                 66.335417   Male   

             location           birth_date  access_rank            join_date  \
26837   chennai,India  1988-10-30 00:00:00          NaN  2014-03-26 00:00:00   
28419  chennai ,India  1997-11-06 00:00:00          NaN  2016-10-04 00:00:00   
87828         chennai  1993-07-20 00:00:00          NaN  2015-03-11 00:00:00   

               last_online  stats_mean_score  stats_rewatched  stats_episodes  \
26837  2018-05-13 12:15:01              7.34              1.0           20143   
28419  2018-04-07 22:27:57              8.50             16.0            6043   
87828  2017-08-10 06:46:00              7.76              2.0            4049   

             t1     t2  
26837   chennai  India  
28419  chennai   India  
87828   chennai    NaN

In [200]:
users['loc_1'] = users['location'].str.split(',').str[0].str.lower().str.strip()
users['loc_2'] = users['location'].str.split(',').str[1].str.lower().str.strip()
users[['location','loc_1','loc_2']].head(20)

location                 loc_1       loc_2
0        Chennai, India                chennai       india
1       Detroit,Michigan               detroit    michigan
2        Nayarit, Mexico               nayarit      mexico
3      Malaysia, Kuantan              malaysia     kuantan
4    Nijmegen, Nederland              nijmegen   nederland
5                 Poland                poland         NaN
6         Norberg Sweden        norberg sweden         NaN
7                 Poland                poland         NaN
8               Nebraska              nebraska         NaN
9     England,Manchester               england  manchester
10           ~ Hungary ~           ~ hungary ~         NaN
11        United Kingdom        united kingdom         NaN
12                  home                  home         NaN
13            California            california         NaN
14                Mexico                mexico         NaN
15      Hamilton Ontario      hamilton ontario         NaN
16           Chicago, IL               chicago          il
17          San Jose, CA              san jose          ca
18  somewhere really hot  somewhere really hot         NaN
19                 Guess                 guess         NaN

In [201]:
users.assign(city=users.loc_1.isin(world_cities.city_ascii))

username  user_id  user_watching  user_completed  user_onhold  \
0               karthiga  2255153              3              49            1   
1              Damonashu    37326             45             195           27   
2                  bskai   228342             25             414            2   
3         terune_uzumaki   327311              5               5            0   
4                  Bas_G  5015094             35             114            6   
5               HimeAria  3129315              2              87            2   
6            Skallington   326733              0               3            0   
7                 Slimak    61677             79             224            0   
8                Elysiun  5927342              7               4            0   
9             jimothy000    47167              6               0            0   
10         MistButterfly  2485327             66            3923          115   
11         ProperBritish   253613              6             233            7   
12               kioniel   144049             11             433            5   
13                 Xinil        1              4             230            8   
14              helenply  2529849              9             184            6   
15              hood_rad  4538087              1             314            0   
16       detestedlove311     5309              3              29            5   
17           ihasabucket    18867              6             146           15   
18           xTheFallenx   340873             22             655            2   
19           L-LawlietDN    14658              5               0            0   
20             zZKinhoZz  6951406             10              65            3   
21           glittermilk   502599             15              35            2   
22             Lithuelle  2637159              3             148            6   
23            scootarski    19539              4             269           10   
24          Yukia-Kontan    60451              1              13            2   
25               Akihara    82964             17             623            2   
26           Tomoki-sama  1933206             10             348           15   
27               Sakurei   158248              4             621           14   
28               raickos   363955             25             172            7   
29                 Spike  4918730              5             353            2   
...                  ...      ...            ...             ...          ...   
108681         NessaIero  3311041              9             242          117   
108682  TsuyoiTamashi231  4714271             12             272            6   
108683         Falco2424  4169795              6             128           53   
108684            Theasn  1200343             52             146            0   
108685        Ray0flight  1756787              8              27           11   
108686    adultswimfan88   328362             15              35            1   
108687            Doraka  2465991              2              26            0   
108688     BlackRockShtr  2508133             31             122            3   
108689          Sadpanda   376282             16             252            0   
108690        FateMaster  3019457            136             524            7   
108691        xsxeotakux   368016              5               6            1   
108692            Perzik  5666502              5              96            5   
108693             Tenos   443061              4             128            0   
108694          Destiney   277365              9              62            3   
108695       Lost_Bullet   549565              2              74            1   
108696            alesos  3476081              4              70            1   
108697          Jarlath7  2604703              2             367          100   
108698       M_Northstar   298302             1

In [202]:
users.loc[users.loc_1.isin(world_cities),'city']= users.loc_1
users.loc[users.loc_1.isin(world_cities),'city']= users.loc_1

In [203]:
world_cities[world_cities['country'] == 'India']

city        city_ascii      lat      lng country iso2 iso3  \
2                 Delhi             Delhi  28.6600  77.2300   India   IN  IND   
3                Mumbai            Mumbai  18.9667  72.8333   India   IN  IND   
13              Kolkāta           Kolkata  22.5411  88.3378   India   IN  IND   
23            Bangalore         Bangalore  12.9699  77.5980   India   IN  IND   
30              Chennai           Chennai  13.0825  80.2750   India   IN  IND   
41            Hyderābād         Hyderabad  17.3667  78.4667   India   IN  IND   
57                 Pune              Pune  18.5196  73.8553   India   IN  IND   
65            Ahmadābād         Ahmadabad  23.0300  72.5800   India   IN  IND   
104               Sūrat             Surat  21.1700  72.8300   India   IN  IND   
233             Lucknow           Lucknow  26.8470  80.9470   India   IN  IND   
254              Jaipur            Jaipur  26.9167  75.8667   India   IN  IND   
296            Cawnpore          Cawnpore  26.4725  80.3311   India   IN  IND   
318            Mirzāpur          Mirzapur  25.1500  82.5800   India   IN  IND   
333              Nāgpur            Nagpur  21.1539  79.0831   India   IN  IND   
338           Ghāziābād         Ghaziabad  28.6667  77.4167   India   IN  IND   
354              Indore            Indore  22.7206  75.8472   India   IN  IND   
378            Vadodara          Vadodara  22.3000  73.2000   India   IN  IND   
383      Vishākhapatnam    Vishakhapatnam  17.7333  83.3167   India   IN  IND   
404              Bhopāl            Bhopal  23.2500  77.4167   India   IN  IND   
434           Chinchvad         Chinchvad  18.6278  73.8131   India   IN  IND   
440               Patna             Patna  25.6100  85.1414   India   IN  IND   
450            Ludhiāna          Ludhiana  30.9083  75.8486   India   IN  IND   
466                Āgra              Agra  27.1800  78.0200   India   IN  IND   
471              Kalyān            Kalyan  19.2502  73.1602   India   IN  IND   
472             Madurai           Madurai   9.9197  78.1194   India   IN  IND   
475          Jamshedpur        Jamshedpur  22.8000  86.1833   India   IN  IND   
493               Nāsik             Nasik  20.0000  73.7833   India   IN  IND   
524           Farīdābād         Faridabad  28.4333  77.3167   India   IN  IND   
532          Aurangābād        Aurangabad  19.8800  75.3200   India   IN  IND   
541              Rājkot            Rajkot  22.2969  70.7984   India   IN  IND   
...                 ...               ...      ...      ...     ...  ...  ...   
14690         Curchorem         Curchorem  15.2500  74.1000   India   IN  IND   
14754           Pushkar           Pushkar  26.5000  74.5500   India   IN  IND   
15299           Barehra           Barehra  27.7500  78.5667   India   IN  IND   
15313            Mundra            Mundra  22.8500  69.7300   India   IN  IND   
15346             Belūr             Belur  13.1642  75.8647   India   IN  IND   
15604         Dharmsāla         Dharmsala  32.2167  76.3167   India   IN  IND   
15911          Rājmahal          Rajmahal  25.0500  87.8400   India   IN  IND   
15942              Kulu              Kulu  31.9600  77.1000   India   IN  IND   
16510              Khed              Khed  17.7200  73.3800   India   IN  IND   
16910     Seven Pagodas     Seven Pagodas  12.6227  80.1939   India   IN  IND   
17175           Konārka           Konarka  19.8878  86.0948   India   IN  IND   
17211      Chīpurupalle      Chipurupalle  18.3000  83.5667   India   IN  IND   
17933           Pondūru           Ponduru  18.3508  83.7567   India   IN  IND   
18055         Pānchgani         Panchgani  17.9200  73.8200   India   IN  IND   
18338            Parigi            Parigi  13.8929  77.4598   India   IN  IND   
18452             Dubak             Dubak  18.1914  78.6783   India   IN  IND   
18457             Betma             Betma  22.6800  75.6200   India   IN  IND   
18749        Khem Karan        Khem Karan  31.1600

In [204]:
if world_cities.country.str.contains('India'):
    print('hi')

ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().

In [205]:
world_cities.dtypes

city           object
city_ascii     object
lat           float64
lng           float64
country        object
iso2           object
iso3           object
admin_name     object
capital        object
population    float64
id              int64
dtype: object

In [206]:
'India'.lower().strip() in world_cities.country.str.lower().str.strip()

False

In [207]:
world_cities.country

0                   Japan
1               Indonesia
2                   India
3                   India
4             Philippines
5                   China
6                  Brazil
7            Korea, South
8                  Mexico
9                   China
10                  China
11                  Egypt
12          United States
13                  India
14                 Russia
15               Thailand
16              Argentina
17                  China
18             Bangladesh
19                Nigeria
20                 Turkey
21                  Japan
22               Pakistan
23                  India
24                   Iran
25       Congo (Kinshasa)
26                Vietnam
27          United States
28                 Brazil
29                  China
               ...       
26532              Russia
26533              Russia
26534              Russia
26535              Russia
26536              Russia
26537              Russia
26538              Russia
26539       

In [208]:
users['city'] = np.nan
users['country'] = np.nan

In [231]:
for index, row in users.iterrows():
    if not pd.isnull(row['loc_1']):
        for ix, rw in world_cities.iterrows():
            if (row['loc_1'] == rw['city_ascii'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first split to city')
                break
            elif (row['loc_2'] == rw['city_ascii'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched second split to city')
                break
            elif (row['loc_1'] == rw['country'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first split to country')
                break
            elif (row['loc_2'] == rw['country'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched second split to city')
                break
            
            whitespace1 = row['location'].split(' ')[0].lower().strip()
            whitespace2 = row['location'].split(' ')[-1].lower().strip()
            if (whitespace1 == rw['city_ascii'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first whitespace1 to city')
                break
            elif (whitespace2 == rw['city_ascii'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first whitespace2 split to city')
                break
            elif (whitespace1 == rw['country'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first whitespace1 split to country')
                break
            elif (whitespace2 == rw['country'].lower()):
                row['city'] = rw['city_ascii']
                row['country'] = rw['country']
                print('Matched first whitespace2 split to country')
                break
        print("completed " + str(index))

Matched second split to city
completed 0
Matched first split to city
completed 1
Matched second split to city
completed 2
Matched first split to country
completed 3
Matched second split to city
completed 4
Matched first split to country
completed 5
Matched first whitespace2 split to country
completed 6
Matched first split to country
completed 7
completed 8
Matched second split to city
completed 9
completed 10
Matched first split to country
completed 11
completed 12
Matched first split to city
completed 13
Matched first split to country
completed 14
Matched first whitespace1 to city
completed 15
Matched first split to city
completed 16
Matched first split to city
completed 17
completed 18
completed 19
completed 20
completed 21
Matched second split to city
completed 22
Matched first whitespace1 to city
completed 23
completed 24
Matched first split to country
completed 25
completed 26
Matched first split to city
completed 27
Matched first split to city
completed 28
Matched first whitespac

completed 217
completed 218
Matched second split to city
completed 219
Matched second split to city
completed 220
completed 221
completed 222
Matched first split to country
completed 223
Matched first split to country
completed 224
completed 225
Matched first split to city
completed 226
completed 227
Matched first split to country
completed 228
Matched first split to country
completed 229
completed 230
Matched second split to city
completed 231
Matched first split to city
completed 232
completed 233
Matched second split to city
completed 234
Matched first split to country
completed 235
Matched second split to city
completed 236
Matched first split to city
completed 237
Matched first split to city
completed 238
completed 239
Matched first split to city
completed 240
Matched second split to city
completed 241
Matched first split to country
completed 242
Matched first split to country
completed 243
Matched second split to city
completed 244
Matched first split to city
completed 245
Matche

Matched first split to city
completed 440
Matched first split to country
completed 441
Matched second split to city
completed 442
Matched first split to city
completed 443
Matched first split to city
completed 444
Matched first split to city
completed 445
Matched first split to country
completed 446
Matched first whitespace2 split to country
completed 447
Matched first split to city
completed 448
completed 449
Matched second split to city
completed 450
Matched first split to city
completed 451
Matched first split to country
completed 452
completed 453
Matched first split to city
completed 454
Matched first split to city
completed 455
Matched first split to country
completed 456
completed 457
Matched first split to country
completed 458
Matched first split to city
completed 459
Matched second split to city
completed 460
Matched first whitespace2 split to city
completed 461
completed 462
Matched second split to city
completed 463
Matched first split to city
completed 464
completed 465
Ma

Matched first split to city
completed 676
Matched first whitespace1 to city
completed 677
Matched first split to city
completed 678
Matched first split to country
completed 679
Matched first split to city
completed 680
Matched first split to country
completed 681
Matched first split to city
completed 682
completed 683
Matched first split to country
completed 684
Matched first split to country
completed 685
Matched first split to country
completed 686
completed 687
completed 688
Matched first split to country
completed 689
Matched first whitespace1 to city
completed 690
Matched first split to country
completed 691
Matched first split to city
completed 692
Matched first split to country
completed 693
Matched first split to country
completed 694
Matched first split to country
completed 695
Matched first split to country
completed 696
Matched first split to country
completed 697
Matched second split to city
completed 698
completed 699
completed 700
Matched first whitespace1 to city
complet

Matched first split to city
completed 900
completed 901
Matched first split to city
completed 902
completed 903
Matched first split to city
completed 904
completed 905
Matched first split to city
completed 906
Matched first split to country
completed 907
Matched first split to city
completed 908
Matched first split to city
completed 909
Matched second split to city
completed 910
Matched first split to country
completed 911
Matched first split to city
completed 912
Matched first split to city
completed 913
Matched first split to country
completed 914
completed 915
completed 916
Matched first split to country
completed 917
completed 918
completed 919
Matched first split to country
completed 920
Matched first split to city
completed 921
Matched first split to city
completed 922
Matched first split to city
completed 923
Matched first split to city
completed 924
Matched first split to city
completed 925
completed 926
Matched first split to country
completed 927
Matched first split to city
c

...

completed 5957
Matched second split to city
completed 5958
Matched first split to country
completed 5959
Matched first split to city
completed 5960
Matched first split to country
completed 5961
completed 5962
Matched second split to city
completed 5963
completed 5964
Matched first split to country
completed 5965
Matched first split to country
completed 5966
Matched first whitespace1 to city
completed 5967
Matched first whitespace2 split to country
completed 5968
completed 5969
Matched first split to city
completed 5970
Matched first split to country
completed 5971
completed 5972
completed 5973
Matched first split to country
completed 5974
Matched first split to city
completed 5975
Matched second split to city
completed 5976
Matched first split to city
completed 5977
Matched first split to city
completed 5978
Matched first split to city
completed 5979
Matched first split to country
completed 5980
Matched second split to city
completed 5981
completed 5982
completed 5983
Matched second sp

completed 6179
completed 6180
completed 6181
completed 6182
completed 6183
completed 6184
Matched first split to city
completed 6185
Matched first split to city
completed 6186
Matched second split to city
completed 6187
Matched first split to city
completed 6188
Matched first split to city
completed 6189
Matched first split to country
completed 6190
Matched first split to city
completed 6191
completed 6192
Matched first split to country
completed 6193
Matched second split to city
completed 6194
Matched first split to country
completed 6195
Matched first split to city
completed 6196
Matched second split to city
completed 6197
Matched first split to city
completed 6198
Matched first split to city
completed 6199
Matched first split to city
completed 6200
Matched first split to city
completed 6201
completed 6202
Matched first whitespace2 split to country
completed 6203
Matched second split to city
completed 6204
Matched first split to country
completed 6205
Matched first split to country
c

Matched first split to city
completed 6404
completed 6405
completed 6406
completed 6407
Matched second split to city
completed 6408
Matched first split to city
completed 6409
Matched first split to city
completed 6410
completed 6411
completed 6412
Matched first split to city
completed 6413
Matched first split to city
completed 6414
completed 6415
Matched first split to city
completed 6416
Matched second split to city
completed 6417
Matched first whitespace2 split to country
completed 6418
completed 6419
Matched first split to country
completed 6420
Matched first split to city
completed 6421
completed 6422
Matched first split to city
completed 6423
completed 6424
Matched first split to city
completed 6425
Matched first split to country
completed 6426
Matched first split to country
completed 6427
Matched first split to city
completed 6428
Matched first split to city
completed 6429
Matched first split to city
completed 6430
Matched first split to city
completed 6431
completed 6432
Matched

completed 6627
Matched first split to country
completed 6628
Matched first split to country
completed 6629
Matched first split to country
completed 6630
completed 6631
completed 6632
Matched second split to city
completed 6633
Matched second split to city
completed 6634
Matched first split to country
completed 6635
Matched first split to city
completed 6636
Matched first split to city
completed 6637
Matched first whitespace2 split to city
completed 6638
completed 6639
Matched first split to city
completed 6640
completed 6641
Matched first split to city
completed 6642
Matched second split to city
completed 6643
completed 6644
completed 6645
completed 6646
Matched first split to city
completed 6647
completed 6648
Matched second split to city
completed 6649
completed 6650
completed 6651
Matched second split to city
completed 6652
Matched first whitespace1 to city
completed 6653
completed 6654
completed 6655
Matched first split to city
completed 6656
Matched first split to country
complete

KeyboardInterrupt: 

In [122]:
for index, row in world_cities.iterrows():
    if ('india' == row['country'].str.lower()):
        print(row['city_ascii'],row['country'])

Tokyo
Jakarta
Delhi
Mumbai
Manila
Shanghai
Sao Paulo
Seoul
Mexico City
Guangzhou
Beijing
Cairo
New York
Kolkata
Moscow
Bangkok
Buenos Aires
Shenzhen
Dhaka
Lagos
Istanbul
Osaka
Karachi
Bangalore
Tehran
Kinshasa
Ho Chi Minh City
Los Angeles
Rio de Janeiro
Nanyang
Chennai
Chengdu
Lahore
Paris
London
Linyi
Tianjin
Shijiazhuang
Baoding
Zhoukou
Lima
Hyderabad
Bogota
Weifang
Nagoya
Wuhan
Heze
Ganzhou
Tongshan
Chicago
Handan
Luanda
Fuyang
Kuala Lumpur
Jining
Dongguan
Hanoi
Pune
Chongqing
Changchun
Zhumadian
Ningbo
Onitsha
Nanjing
Hefei
Ahmadabad
Hong Kong
Khartoum
Nantong
Yancheng
Foshan
Nanning
Hengyang
Xi'an
Shenyang
Tangshan
Shaoyang
Changsha
Santiago
Zhengzhou
Zhanjiang
Riyadh
Cangzhou
Dar es Salaam
Maoming
Huanggang
Xinyang
Shangrao
Luoyang
Bijie
Yantai
Quanzhou
Hangzhou
Miami
Kunming
Nanchong
Zunyi
Lu'an
Yichun
Madrid
Taizhou
Liaocheng
Qujing
Xiangyang
Surat
Baghdad
Qingdao
Singapore
Dallas
Changde
Dazhou
Suzhou
Philadelphia
Jieyang
Nairobi
Nangandao
Ankara
Tai'an
Yulin
Dezhou
Houston
At

Yicheng
Tabuk
Lipetsk
Ulhasnagar
Matsuyama
Muntinlupa City
Kashgar
Linghai
Aden
Jhansi
Kitwe
Aba
Palm Bay
Pingtung
Samarkand
Davangere
Ichikawa
Jammu
Mazatlan
Higashi-osaka
Ile-Ife
Kirov
Madinat as Sadis min Uktubar
Qaraghandy
Mazatan
Duisburg
Mykolaiv
Matsudo
Provo
Meicheng
Niteroi
Rouen
Oujda-Angad
Johor Bahru
Worcester
Hongjiang
Chimbote
Dengtacun
Ixtapaluca
Zhijiang
Chengjiao
Beipiao
Murrieta
Kota Bharu
Heshan
Ciudad Lopez Mateos
Vinh
Tultitlan de Mariano Escobedo
Duyun
Encheng
Nishinomiya-hama
Kandahar
Cheboksary
Yuanping
Port Sudan
Valledupar
Edinburgh
Belgaum
Tula
Taozhou
Suez
Shahe
Yazd
Nazret
Gaoping
Brookhaven
Greenville
Arak
San Nicolas de los Garza
Gulbarga
Juiz de Fora
Dunhua
Feira de Santana
Jiaji
Az Zarqa'
Americana
Ardabil
Sylhet
Wichita
Toledo
Kaihua
Caerdydd
Jamnagar
Fuyuan
Dhulia
Nampula
Gaya
Piraeus
Oita
Florianopolis
Chiniot
Jiannan
Wuhai
Kaliningrad
Sukkur
Nangong
Staten Island
San Juan
Vila Velha
Macapa
Des Moines
Piura
Jiaojiangcun
Laohekou
Fujin
Beian
Celaya
Xi

Santiago del Estero
Usak
Begusarai
North Las Vegas
Sonipat
Los Teques
Mabalacat
Jinshi
Osh
Iwo
Bata
Chofugaoka
Komsomol'sk-na-Amure
Babol
Galati
Al Bayda'
Yamagata
Manzhouli
Kiel
Braunschweig
Rivne
Gdynia
Palangkaraya
Al Minya
Hafr al Batin
Caruaru
San Bernardo
Bukan
Aachen
Sahiwal
Chigasaki
Thu Dau Mot
Sibu
Anchorage
Parana
Oruro
Merlo
Syktyvkar
Khimki
Biratnagar
Chemnitz
Saskatoon
Yato
Colon
Abertawe
Fuji
Puerto Montt
Jessore
Beichengqu
Tuy Hoa
Shrirampur
Chesapeake
Hapur
Bahir Dar
Manisa
Tanga
Sabzevar
Ramgundam
Porto
Tacloban
Myitkyina
Barnstable
Haeju
Petah Tiqwa
Norfolk
Gonzalez Catan
Juazeiro do Norte
Diaobingshancun
Tarapoto
Zhangping
San Juan del Rio
Tsukuba-kenkyugakuen-toshi
Sao Carlos
Ilheus
Fremont
Halle
Duzce
Anju
Aarhus
Kennewick
Hobart
Artux
Chimoio
Limassol
Garland
Magdeburg
Irving
Hachimancho
Longueuil
Mokpo
Kosice
`Ajman
Lille
Neya
Banda Aceh
Le Havre
Taiping
P'yong-dong
Springs
Ivano-Frankivsk
As Sib
Narayanganj
Wuyishan
Sato
Amol
Quilmes
Mirpur Khas
Nizhnekamsk
Vis

Shantipur
Kukichuo
Golmeh
Zabid
Peristeri
Hindupur
Sunnyvale
Baubau
Mudon
Sayama
Taza
Settat
Imabari
Foggia
Erode
Pocos de Caldas
Gwangyang
Tororo
Gonbad-e Kavus
Al Manaqil
Miass
Tulancingo
Nimes
Chinandega
Saint Albans
Nakhodka
Quevedo
Bintulu
Pomona
Siem Reap
Escondido
Cao Lanh
Riobamba
Vryheid
As Suwayhirah as Sahil
Paderborn
Zamora
Manzanillo
Pasadena
Florencio Varela
Komaki
Talcahuano
Kerch
Patos de Minas
Copiapo
Badajoz
M'Sila
Kragujevac
Pointe-a-Pitre
Willemstad
Rimini
Dundee
Jijel
Ocumare del Tuy
Valdivia
Gulu
La Ceiba
Shahrud
Iruma
Kashikishi
Sumbawanga
Keren
Odivelas
New Bedford
Jamuria
Kutaisi
Potchefstroom
Shimotoda
Concordia
Abbottabad
Delicias
Mallawi
Agri
Amasya
Lang Son
Salamanca
Kastamonu
Marvdasht
Goma
Yonago
Chingola
Fairfield
Mostaganem
Habra
Mauli
Sibiu
Naperville
Quilpue
Dolores Hidalgo Cuna de la Independencia Nacional
Kopeysk
Luleburgaz
Al Hawiyah
Bellevue
Binghamton
Nchelenge
Negombo
Ambala
Disuq
Mangghystau
Malakal
Bacau
Osorno
Elkhart
Topeka
Mogi Guacu
Man
Jo

South Shields
Paisley
Weston-super-Mare
Goiana
Bilecik
Juchitan de Zaragoza
Buena Park
Saint-Maur-des-Fosses
Hakkari
Somerville
Chalandri
Bury
Tres Lagoas
Jatai
Gravesend
Aviles
Deerfield Beach
Targoviste
Altamira
Galway
Natitingou
Sao Joao del Rei
Barreiro
Paysandu
Cicero
Atakpame
Focsani
Palmerston North
Iguatu
Drancy
Adigrat
Zuwarah
Shancheng
Sidi Qacem
Puerto Ayacucho
Lawrence
Erdenet
Rubi
Temoaya
Ouahigouya
Silver Spring
Nakhon Pathom
Lowestoft
Pau
Tejupilco
Cheyenne
Ubon Ratchathani
Tustin
Lakewood
Carlisle
Lisala
Szombathely
Banska Bystrica
Ra`ananna
Harrogate
Aveiro
Tambacounda
Newcastle under Lyme
Inowroclaw
New Rochelle
Kensington
La Rochelle
Lebanon
East Kilbride
Wa
Nitra
Lomas del Mirador
Maghaghah
Mpanda
Bacabal
Gladbeck
Sankt Gallen
Cachoeira do Sul
Campo Mourao
Cannes
Alameda
Thornton Heath
Watsonville
Taluqan
Juventino Rosas
Jinja
Davis
Berberati
Esbjerg
Zrenjanin
Las Piedras
Surt
Tamazunchale
Pancevo
Chiryu
Abeche
Bellflower
Ashford
Bokhtar
Musashimurayama
Nek'emte
Cal

...

Kutztown
Zavolzhsk
Progress Village
Fairview Township
Schotten
Steinhaus
Fort Madison
Salaverry
Danville
Tsuno
Keuruu
Vienna
Manville
Kirkland
Bel Air
Old Saybrook
Warr Acres
Franklin
Rudesheim am Rhein
Judenburg
Tipp City
Klotze
Lincoln Park
Struthers
Chapel en le Frith
North Glengarry
Kurort Steinbach-Hallenberg
Satipo
Digora
Waldwick
Shawano
Mountsorrel
Nogliki
Nideggen
South Huron
Mengen
Marieville
Ontario
Lysa nad Labem
Cedar Hills
Hobart
North Versailles
Oldenburg in Holstein
Crigglestone
Conway
Cresson
Makale
Clinton
Southborough
Standish
Edwards
Garden City
Nolensville
Glocester
Camden
Kargopol'
Wood River
Akabira
Ollerton
Kubrat
Sleepy Hollow
Milford Township
Sankt Andra
Surany
Fair Oaks Ranch
Countryside
Hlinsko
Robore
Valea lui Mihai
Vashon
Moba
Holmen
Santa Maria Ajoloapan
Tay
Alden
Coweta
Ohrdruf
Warrenton
Volodarsk
Purkersdorf
Pleasant Hill
Taltal
Vuktyl
Senanga
Alajarvi
Aveley
Byalynichy
Bee Ridge
Pyetrykaw
Laurens
Uchoa
Flat Rock
Molalla
Gar
South Huntington
Bude
Fairmo

Willowbrook
Irondale
Whitworth
Springfield
Green Cove Springs
Kellinghusen
Rhos-on-Sea
Lake Villa
North Madison
Colditz
Guntersville
Lansdowne
Karumai
Montvale
Aspen
Joane
Brooksville
Fairfield Glade
Sanatoga
Riverside
Wyoming
Staufen im Breisgau
West Frankfort
Chos Malal
Mamurras
Pochinok
Indian Harbour Beach
Dzhebel
Helmbrechts
Lake Park
Murten
Lanco
Kildare
Lucas
Piedmont
Barton
Franklin
Innsbrook
Chumsaeng
Obluch'ye
Conover
Coxsackie
Mournies
Dulovo
Litchfield
Mansfield
Wetumpka
Lossnitz
Ladysmith
Conkal
Laitila
Divjake
East Grand Forks
Bridgewater
Krupki
Guaracai
Park Hills
Messkirch
Laurel
Cullompton
Freistadt
Mooroopna
Rawlins
Morrisville
Negresti
Odessa
Narrabri
Plumsted
White Horse
Yatton
Closter
Perryton
St. Johns
Worrstadt
Frostburg
Kingscliff
Concord
Lacombe
Lypovets'
Dunavarsany
Rolesville
Yarmouth
Biryusinsk
Bo`ston
Mina Clavero
Viechtach
Turkeve
Neuenburg
Vohburg an der Donau
Southampton Township
Incline Village
Campo Maior
San Sebastian
Bolgar
Visp
Namsos
Billingshurst


Slavkov u Brna
Ibirarema
Nambu
Tornal'a
Providence Village
Webster City
Inverness
Clarkston
Arraiolos
Smithfield Township
Middlesex
Tolleson
Groditz
New Roads
Ponchatoula
Strathalbyn
Oroville East
Mapimi
Slivnitsa
Poiares
Plumas Lake
Winsted
Skiatook
Santa Marta de Penaguiao
Humberston
Buena Vista
New Hanover
Bannockburn
Wolkersdorf im Weinviertel
Coeymans
Pomona
Houston
Charles City
Dettelbach
Ulmeni
Turceni
Frankstown
Yreka
Harjavalta
Stanwood
Augusta
Leola
Canovanas
St. Joseph
Taga
Abersychan
Sergeevka
Crumlin
Hudsonville
Ebern
Spring Hill
Philadelphia
Chalastra
Bellbrook
Northridge
Zbaszyn
Dayton
Hampden
Seymour
Gibsonville
Parsberg
Elzach
Dade City
Southgate
Fresia
Nortorf
Greenville
Puslinch
Schesslitz
Pogoanele
Lavrio
Winooski
Middleborough Center
Rockville
Whaley Bridge
Kuklen
East Pikeland
Wriezen
Sturry
Rabaul
East Marlborough
Homeland
Bryans Road
Valley Center
New Sewickley
Vila Nova da Barquinha
Ormond-by-the-Sea
Cannington
Umatilla
Cehu Silvaniei
Strasburg
Oak Grove
Waucho

Bellwood
Homeland Park
Mnisek pod Brdy
Wilna
Chatham
Wassertrudingen
De Queen
Evansville
Cocoa West
Clinton
Pardinho
Lanett
Gardnerville
Ujszasz
Bridgewater
Comstock Northwest
East Farmingdale
Glenarden
Plainfield
New Norfolk
Southampton
Dornhan
Cullowhee
Tequesta
Broughton
Elm Grove
Heber Springs
Ashton-Sandy Spring
Waimanalo
Welshpool
Carlstadt
Lebanon
Sumeg
Carrollton
Cochran
Sedgefield
Helmshore
Hurley
Novokhopersk
Jambeiro
Shikhany
Lower Nazareth
Braunlage
Garrettsville
Kozaki
Isanti
Taciba
Otaci
Sky Lake
Marcellus
Punxsutawney
Brigg
Dunlap
Beacon Falls
Bartonville
Ixcateopan de Cuauhtemoc
Laie
Saint-Apollinaire
Munford
Tarrant
Woodville
Santo Antonio do Jardim
Los Ranchos de Albuquerque
Megalopoli
Perrenjas
Edgewood
Windsbach
Rindge
Scenic Oaks
Bresje
Mattydale
Shihoro
Ts'nori
Tillicoultry
Amory
Ranchettes
Rio Espera
Jordan
Filiatra
Janossomorja
Hordle
Simsbury Center
Shrewsbury
Adlington
Madalena
Riedenburg
Alpine
Harlan
Hindon Hill
East Ballina
Dinguiraye
Krume
Willard
Senatobi

Simonton Lake
Lone Grove
Colona
Negru Voda
Halac
Montecastrilli
Dmitrovsk-Orlovskiy
Adams
Spalt
Guzolandia
Suncook
Carmi
Oberviechtach
Shelby
Ilok
Gargalianoi
Mexico
Shanor-Northvue
Utica
San Leon
Schuylkill Haven
Hollfeld
Horsovsky Tyn
Poplar Grove
Scott City
Portland
Naumburg
Bozhurishte
Buellton
Daleville
Belleview
Chadron
Westlock
Marion
Ostrov
West Mead
Temiscouata-sur-le-Lac
Sousel
Brownfields
Candor
Shannon
Colesville
Osoyoos
Vale
Rio Hondo
Lyubim
North Fond du Lac
Crestwood
Paradise Hills
Isaccea
Fox Chapel
Colebrookdale
Nisekoan
Midway North
Offutt AFB
Canterbury
De Motte
Laraquete
Scott Township
Glencoe
McKenzie
Hearst
Rockingham
Alfred
Middle Paxton
Bay Hill
Shipston on Stour
Doffing
Kings Park
Alvaro de Carvalho
Munroe Falls
Canutillo
Monee
Williamston
Ipigua
Buckley
Gretna
Wayne Township
Lower Oxford
Bronnoysund
Stewartstown
Garnet
Baile Herculane
Jericho
Clifton
Pratania
Livingston
Springfield Township
Berkeley
Vancleave
Deerfield
Carver
Yarmouth Port
Dundee
Summit
Morgan

### Convert world cities into a dictionary

In [ ]:
json_world = world_cities['city_ascii'].to_json(orient='index')

In [240]:
json_world

'{"0":"Tokyo","1":"Jakarta","2":"Delhi","3":"Mumbai","4":"Manila","5":"Shanghai","6":"Sao Paulo","7":"Seoul","8":"Mexico City","9":"Guangzhou","10":"Beijing","11":"Cairo","12":"New York","13":"Kolkata","14":"Moscow","15":"Bangkok","16":"Buenos Aires","17":"Shenzhen","18":"Dhaka","19":"Lagos","20":"Istanbul","21":"Osaka","22":"Karachi","23":"Bangalore","24":"Tehran","25":"Kinshasa","26":"Ho Chi Minh City","27":"Los Angeles","28":"Rio de Janeiro","29":"Nanyang","30":"Chennai","31":"Chengdu","32":"Lahore","33":"Paris","34":"London","35":"Linyi","36":"Tianjin","37":"Shijiazhuang","38":"Baoding","39":"Zhoukou","40":"Lima","41":"Hyderabad","42":"Bogota","43":"Weifang","44":"Nagoya","45":"Wuhan","46":"Heze","47":"Ganzhou","48":"Tongshan","49":"Chicago","50":"Handan","51":"Luanda","52":"Fuyang","53":"Kuala Lumpur","54":"Jining","55":"Dongguan","56":"Hanoi","57":"Pune","58":"Chongqing","59":"Changchun","60":"Zhumadian","61":"Ningbo","62":"Onitsha","63":"Nanjing","64":"Hefei","65":"Ahmadabad","6

In [257]:
world_cities["lower_city"] = world_cities["city_ascii"].str.lower()
world_cities["lower_country"] = world_cities["country"].str.lower()
dict_world = world_cities.set_index('lower_city')['lower_country'].T.to_dict()

In [258]:
dict_world

{'tokyo': 'japan',
 'jakarta': 'indonesia',
 'delhi': 'united states',
 'mumbai': 'india',
 'manila': 'philippines',
 'shanghai': 'china',
 'sao paulo': 'brazil',
 'seoul': 'korea, south',
 'mexico city': 'mexico',
 'guangzhou': 'china',
 'beijing': 'china',
 'cairo': 'united states',
 'new york': 'united states',
 'kolkata': 'india',
 'moscow': 'united states',
 'bangkok': 'thailand',
 'buenos aires': 'costa rica',
 'shenzhen': 'china',
 'dhaka': 'bangladesh',
 'lagos': 'portugal',
 'istanbul': 'turkey',
 'osaka': 'japan',
 'karachi': 'pakistan',
 'bangalore': 'india',
 'tehran': 'iran',
 'kinshasa': 'congo (kinshasa)',
 'ho chi minh city': 'vietnam',
 'los angeles': 'chile',
 'rio de janeiro': 'brazil',
 'nanyang': 'china',
 'chennai': 'india',
 'chengdu': 'china',
 'lahore': 'pakistan',
 'paris': 'united states',
 'london': 'united states',
 'linyi': 'china',
 'tianjin': 'china',
 'shijiazhuang': 'china',
 'baoding': 'china',
 'zhoukou': 'china',
 'lima': 'united states',
 'hyderaba

In [276]:
if 'chennai' in dict_world.keys():
    print(dict_world['chennai'])

india


# Final Extraction Method: Success 

In [304]:
city = []
country = []

import time
start = time.time()

for index, row in users.iterrows():
    if not pd.isnull(row['loc_1']):
        if row['loc_1'] in dict_world.values():
#             row['city'] = row['loc_1']
            city.append(None)
            country.append(row['loc_1'])
            print('Matched first split to country')
            continue
        elif row['loc_2'] in dict_world.values():
#             row['city'] = row['loc_2']
            city.append(None)
            country.append(row['loc_2'])
            print('Matched second split to country')
            continue
        elif row['loc_1'] in dict_world.keys():
            city.append(row['loc_1'])
            country.append(dict_world[row['loc_1']])
            print('Matched first split to city')
            continue
        elif row['loc_2'] in dict_world.keys():
            city.append(row['loc_2'])
            country.append(dict_world[row['loc_2']])
            print('Matched second split to city')
            continue
            
        whitespace1 = row['location'].split(' ')[0].lower().strip()
        whitespace2 = row['location'].split(' ')[-1].lower().strip()
        if whitespace1 in dict_world.values():
            city.append(None)
            country.append(whitespace1)
            print('Matched first whitespace1 to country')
            continue
        elif whitespace2 in dict_world.values():
            city.append(None)
            country.append(whitespace2)
            print('Matched first whitespace2 split to country')
            continue
        elif whitespace1 in dict_world.keys():
            city.append(whitespace1)
            country.append(dict_world[whitespace1])
            print('Matched first whitespace1 to city')
            continue
        elif whitespace2 in dict_world.keys():
            city.append(whitespace2)
            country.append(dict_world[whitespace2])
            print('Matched first whitespace2 split to city')
            continue
    city.append(None)
    country.append(None)
    print("completed " + str(index))

users['city'] = city
users['country'] = country

end = time.time()
print(end - start)

Matched second split to country
Matched first split to city
Matched second split to country
Matched first split to country
Matched second split to city
Matched first split to country
Matched first whitespace2 split to country
Matched first split to country
completed 8
Matched second split to city
completed 10
Matched first split to country
completed 12
Matched first split to city
Matched first split to country
Matched first whitespace1 to city
Matched first split to city
Matched first split to city
completed 18
completed 19
completed 20
completed 21
Matched second split to country
Matched first whitespace1 to city
completed 24
Matched first split to country
completed 26
Matched second split to country
Matched first split to city
Matched first whitespace1 to city
Matched second split to country
completed 31
Matched first split to country
Matched second split to country
completed 34
Matched second split to country
Matched second split to country
Matched first split to city
Matched first 

Matched first split to city
Matched second split to country
completed 372
Matched first split to country
completed 374
completed 375
completed 376
Matched second split to country
Matched first split to country
Matched first split to city
Matched second split to country
Matched first whitespace1 to city
Matched first split to country
completed 383
Matched first split to country
Matched second split to country
completed 386
Matched first split to city
Matched first split to city
completed 389
completed 390
Matched first split to country
Matched first split to country
Matched second split to country
Matched first split to country
Matched first whitespace2 split to country
Matched first split to country
completed 397
Matched first split to city
Matched first split to city
Matched first split to country
Matched first whitespace2 split to city
completed 402
Matched first split to city
Matched second split to city
completed 405
Matched first whitespace1 to country
Matched first split to count

completed 742
Matched first split to city
Matched first split to city
Matched first split to city
Matched first split to country
Matched first whitespace2 split to city
completed 748
completed 749
Matched first split to country
Matched second split to country
completed 752
Matched first split to country
Matched first split to city
Matched first split to city
Matched first split to country
completed 757
Matched first whitespace2 split to country
Matched second split to country
Matched first split to country
completed 761
Matched first split to country
Matched second split to country
Matched second split to city
Matched first split to city
Matched first whitespace1 to city
completed 767
Matched first split to city
Matched second split to country
completed 770
Matched first split to country
Matched first split to city
Matched first split to country
completed 774
Matched second split to country
completed 776
Matched second split to country
Matched first split to country
Matched second spli

Matched second split to country
Matched first split to city
Matched first split to country
Matched first split to city
Matched second split to country
Matched first whitespace1 to city
Matched second split to country
Matched first whitespace1 to country
completed 1088
Matched second split to country
Matched second split to country
completed 1091
Matched first split to country
completed 1093
Matched first whitespace2 split to city
Matched first split to country
Matched first split to country
Matched first whitespace2 split to country
Matched first split to country
Matched second split to country
Matched first whitespace2 split to city
Matched first split to country
Matched first split to country
Matched first split to city
completed 1104
Matched first split to city
Matched second split to country
Matched first split to city
Matched first split to country
completed 1109
Matched second split to country
Matched first split to city
Matched first split to country
Matched first split to city


completed 1395
Matched first split to country
completed 1397
completed 1398
Matched first split to country
Matched first split to city
completed 1401
completed 1402
completed 1403
Matched first split to country
Matched second split to country
Matched first split to country
Matched second split to country
Matched first split to country
Matched second split to country
Matched first split to city
Matched first split to country
Matched first split to city
Matched first split to country
Matched first split to country
completed 1415
Matched second split to country
Matched second split to country
Matched first split to city
completed 1419
Matched second split to country
Matched second split to country
Matched second split to country
Matched first split to city
Matched first whitespace2 split to country
Matched first split to city
Matched second split to country
Matched first split to city
completed 1428
Matched first split to city
completed 1430
Matched second split to country
completed 1432


...

completed 107016
Matched second split to country
completed 107018
completed 107019
completed 107020
Matched first split to city
completed 107022
Matched first whitespace2 split to country
Matched first split to city
Matched second split to country
Matched first split to city
Matched first split to country
Matched first split to country
Matched first split to country
completed 107030
completed 107031
Matched second split to country
Matched first split to country
Matched first split to city
Matched first split to city
Matched second split to city
completed 107037
Matched first split to country
Matched second split to country
Matched first split to city
completed 107041
completed 107042
Matched first split to city
Matched first split to country
Matched first split to city
Matched first split to city
Matched second split to city
completed 107048
Matched first split to country
Matched first split to country
Matched first split to city
Matched second split to country
Matched first whitespace

Matched first split to city
Matched second split to country
Matched first split to city
completed 107442
Matched second split to country
Matched second split to country
Matched second split to country
Matched second split to country
Matched first split to city
completed 107448
Matched first split to city
Matched second split to country
Matched first split to country
Matched first whitespace1 to country
completed 107453
Matched second split to country
Matched first split to city
Matched second split to country
Matched second split to country
Matched first split to country
Matched first split to country
Matched first split to country
Matched first split to city
Matched first split to country
Matched first split to city
Matched first split to city
Matched first split to country
Matched first split to country
Matched first split to country
Matched first split to city
Matched first split to city
Matched second split to country
Matched second split to country
completed 107472
completed 10747

Matched first whitespace1 to city
Matched second split to country
Matched first split to city
Matched first split to country
Matched first split to country
Matched first split to city
Matched second split to country
Matched first split to city
Matched second split to country
Matched first split to country
completed 107841
completed 107842
Matched second split to country
completed 107844
Matched first split to country
completed 107846
completed 107847
Matched first split to city
completed 107849
Matched second split to country
completed 107851
Matched first split to city
Matched first split to country
Matched first split to country
Matched first split to country
Matched second split to country
Matched second split to country
Matched first split to city
Matched first split to country
Matched second split to country
Matched second split to country
Matched first whitespace2 split to country
Matched second split to country
Matched second split to country
Matched first split to country
Match

Matched second split to country
Matched first split to country
Matched first split to city
completed 108295
Matched first whitespace2 split to city
completed 108297
Matched first split to country
Matched second split to country
Matched first split to city
Matched second split to country
completed 108302
completed 108303
Matched first split to city
completed 108305
completed 108306
Matched first split to country
Matched first split to city
Matched first split to city
Matched first split to city
Matched first split to country
Matched first split to country
completed 108313
Matched first split to country
Matched first split to city
completed 108316
Matched second split to country
Matched first split to country
completed 108319
Matched first split to city
completed 108321
Matched second split to city
Matched first split to city
Matched second split to country
Matched first split to country
Matched first split to city
Matched first split to city
Matched first split to city
Matched first spl

Matched first split to city
Matched first split to city
Matched first split to country
Matched first split to city
Matched first split to country
Matched first split to country
Matched first split to country
Matched second split to country
Matched first split to city
completed 108631
Matched second split to city
Matched second split to country
Matched first split to country
Matched first split to city
Matched first split to city
Matched first split to city
completed 108638
completed 108639
completed 108640
Matched first split to country
completed 108642
Matched first split to country
Matched first split to city
Matched second split to country
completed 108646
Matched second split to country
Matched first split to city
Matched second split to country
completed 108650
Matched second split to country
Matched first split to city
Matched first split to city
Matched first split to country
Matched first split to city
completed 108656
Matched second split to country
Matched first split to city

In [305]:
users.head(100)

username  user_id  user_watching  user_completed  user_onhold  \
0          karthiga  2255153              3              49            1   
1         Damonashu    37326             45             195           27   
2             bskai   228342             25             414            2   
3    terune_uzumaki   327311              5               5            0   
4             Bas_G  5015094             35             114            6   
5          HimeAria  3129315              2              87            2   
6       Skallington   326733              0               3            0   
7            Slimak    61677             79             224            0   
8           Elysiun  5927342              7               4            0   
9        jimothy000    47167              6               0            0   
10    MistButterfly  2485327             66            3923          115   
11    ProperBritish   253613              6             233            7   
12          kioniel   144049             11             433            5   
13            Xinil        1              4             230            8   
14         helenply  2529849              9             184            6   
15         hood_rad  4538087              1             314            0   
16  detestedlove311     5309              3              29            5   
17      ihasabucket    18867              6             146           15   
18      xTheFallenx   340873             22             655            2   
19      L-LawlietDN    14658              5               0            0   
20        zZKinhoZz  6951406             10              65            3   
21      glittermilk   502599             15              35            2   
22        Lithuelle  2637159              3             148            6   
23       scootarski    19539              4             269           10   
24     Yukia-Kontan    60451              1              13            2   
25          Akihara    82964             17             623            2   
26      Tomoki-sama  1933206             10             348           15   
27          Sakurei   158248              4             621           14   
28          raickos   363955             25             172            7   
29            Spike  4918730              5             353            2   
..              ...      ...            ...             ...          ...   
70      AlexTheRiot  1473307             13             621           27   
71       VoliMedjed  1466623              5              10            1   
72  kennethmusicman  1384947              4             347            0   
73          namiSWN   149817              0             152            4   
74       haeworlddd   375026              3              66           31   
75         Jiraiyan  4543429              6              39            0   
76       IoriYagami    83582              3             141            7   
77         Sirdante    14013             43             372            4   
78           p0nch0    32044              4               2            1   
79       lolbridget  5341448              7              47            6   
80        myungyare  3771925             33             260           19   
81             Tofs    82645              8              27            4   
82         kendolli   300808             33             217            2   
83     lollypebbles   214621              0               2            3   
84   Artistichooves  4457732             12             144            2   
85      redragon777   325327              1               1            0   
86    climhazzard03     3895              1             716            1   
87        bakawingx    46743              3             402           10   
88         werlwend   192396             39             528            7   
89     nighthawk741   401053            160             203           34   
90      watchfuleye  6246569             23              28

In [312]:
users['country'].value_counts()

united states                        19707
poland                                4852
brazil                                4087
canada                                3926
philippines                           2854
germany                               2567
russia                                2531
australia                             2385
indonesia                             2189
france                                1872
portugal                              1760
netherlands                           1728
united kingdom                        1659
sweden                                1567
spain                                 1136
italy                                 1126
romania                               1124
finland                               1077
norway                                1040
japan                                  931
india                                  910
chile                                  854
mexico                                 834
turkey     

In [310]:
world_cities[world_cities['city_ascii'] == 'nebraska']

Empty DataFrame
Columns: [city, city_ascii, lat, lng, country, iso2, iso3, admin_name, capital, population, id, lower_city, lower_country]
Index: []

In [321]:
users.loc[users['username'].isnull()]

username  user_id  user_watching  user_completed  user_onhold  \
51311      NaN   300142             12             158            8   

       user_dropped  user_plantowatch  user_days_spent_watching gender  \
51311            21                62                 39.304167   Male   

      location   ...            last_online  stats_mean_score stats_rewatched  \
51311   Serbia   ...    2018-05-20 04:06:06              6.58            30.0   

      stats_episodes      t1   t2   loc_1 loc_2  city country  
51311           2524  Serbia  NaN  serbia   NaN  None  serbia  

[1 rows x 23 columns]

In [324]:
users = users.drop(columns=['t1','t2','loc_1','loc_2'])

In [325]:
users.columns

Index(['username', 'user_id', 'user_watching', 'user_completed', 'user_onhold',
       'user_dropped', 'user_plantowatch', 'user_days_spent_watching',
       'gender', 'location', 'birth_date', 'access_rank', 'join_date',
       'last_online', 'stats_mean_score', 'stats_rewatched', 'stats_episodes',
       'city', 'country'],
      dtype='object')

In [326]:
users.to_csv('users_cleaned_with_location.csv')

# Location extraction Strategy

### Limitations with location column
- Location column is a user level input and has no structure. Values can be cities, countries, states, non-existent locations. 

## Regex Split String

- Most values in location field are well formatted with existing cities/countries. The first attempt to split the string by commas or whitespaces, separates the location field but there is no guarantee what value you extracted: city, country, state, region etc.

## API calls for Geo libraries
Using geopy, a Python client for several popular geocoding web services, there were a few services experimented.


### Nominatim geocoder for OpenStreetMap data.
By passing in the full value from location field, Nominatim geocoder was successfully able to extract the address such as passing "detroit michigan" results in "Detroit, Wayne County, Michigan, United States of America". This has a usable structure with the first value before comma being city, and the last value after comma being country. However there are over 100,000 rows of locations and Nominatim has a rate limit of 1 request/second. It would require the script to run over 24+ hours. This was attempted however, OpenStreetMap data disconnected due to such a long request period from the same app.

### Google Maps v3 API

Google Maps' Geocoding API uses a pay-as-you-go pricing model. In addition to this they have a 2,500 query/day limit on free/trial plan.

### Using a CSV of top 25,000 most popular cities and countries

Using a csv of cities and countries, a python dictionary was created with city being keys and country as values. By iterating through each comma separated or whitespace separated value from the location column, we can query the world dictionary in O(1) by keys or values to find matching cities or countries. The time complexity of this method is O(n) as we have to iterate through the full dataframe. This method successfully found countries for 75% of the dataset. However, the results are not perfect and are best approximation as value of "Paris" could be "Paris, France" "Paris, Canada" or "Paris, United States". The selected method picks the most popular location based on the "worldcities.csv" file.



